# Setup

In [ ]:
# %run ./include
%pip install polars rich ezregex

Python interpreter will be restarted.
  Attempting uninstall: pygments
    Found existing installation: Pygments 2.11.2
    Not uninstalling pygments at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-22babfc2-df75-4d2d-8ab6-db7563cd35e0
    Can't uninstall 'Pygments'. No files were found to uninstall.
Python interpreter will be restarted.


In [ ]:
import re

import datetime as dt
from rich import print
import polars as pl
import plotly.express as px
import requests
import pyspark.sql.functions as sf
import ezregex as er
# Databricks handles the first two imports.

# access to the sql functions https://spark.apache.org/docs/latest/api/python/pyspark.sql.html#module-pyspark.sql.functions
from pyspark.sql import functions as sf 
from rich import print
import json
import polars as pl
import plotly.express as px
from datetime import datetime, timedelta
# Because Spark is stupid
from copy import deepcopy
# from pyspark.sql.dataframe import DataFrame
import pyspark
print('Imported libraries')

Imported libraries

In [ ]:
patterns = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/patterns/')
spatial = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/spatial/')
places = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/places/')
tract_table = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/tract_table/')
censusblock_table = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/censusblock_table')
censustract_pkmap = spark.read.format('delta').load('dbfs:/user/hive/warehouse/safegraph.db/censustract_pkmap')
# These 3 are manually loaded in by me, because they take a while to generate, or require a specific account to generate
# Source: My webscraper scraping off of https://local.churchofjesuschrist.org/en/us/
addresses = spark.read.csv('dbfs:/FileStore/Attempt3_6509_addresses.csv')
# Source: Scraping the table off of https://pe.usps.com/text/pub28/28apc_002.htm
abbr = pl.DataFrame(spark.read.csv('dbfs:/FileStore/postalTable.csv').toPandas())
# Source: My webscraper + google maps address validation API
fullAddr = spark.read.parquet('dbfs:/FileStore/full_church_building_data_20.parquet')


# Join church buildings with safegraph data

## Method 1: Join on addresses

In [ ]:
abbrs = {}
for i in abbr.select('_c0', '_c2').to_dicts()[2:]:
    abbrs[i['_c0'].lower()] = i['_c2'].lower()
abbrs['bayou'] = 'byu'
abbrs.update({
    'south': 's',
    'north': 'n',
    'east': 'e',
    'west': 'w',
})
abbrs

In [ ]:
# TODO: 
# 1 & main
# things like pine road and mountainview road get abbreviated -- but also, they get abbreviated the same way, so oh well?
# There's a 840 w midway st and an 841 w midway st
# @udf
def formatAddress(col):
    # Remove excess whitespace and lower all letters
    col = sf.trim(sf.lower(sf.col(col)))

    # Replace all common replacements
    for name, abr in abbrs.items():
        col = sf.regexp_replace(col, name, abr)

    # The only whitespace we want are single spaces
    col = sf.regexp_replace(col, er.whitechunk.str(), ' ')
    
    # I think these still don't work quite right...
    # Remove any 1st, 3rd, 5 th, etc.
    # col = sf.regexp_replace(col, (er.group(er.number) + er.optional(er.space) + er.anyof('st', 'rd', 'th')).str(), er.replace_group(1).str())
    # col = sf.regexp_replace(col, (er.namedGroup('num', er.number) + er.optional(er.space) + er.anyof('st', 'rd', 'th')).str(), '${num}')
    # col = sf.regexp_replace(col, (er.group(er.number) + er.optional(er.space) + er.anyof('st', 'rd', 'th')).str(), '\1')
    col = sf.regexp_replace(col, (er.ifPrecededBy(er.number) + er.optional(er.space) + er.anyof('st', 'rd', 'th')).str(), '')

    # Add a space between any 232n or 343s
    # col = sf.regexp_replace(col, (er.group(er.number) + er.group(er.anyof(*list('nsew')))).str(), (er.replace_group(1) + ' ' + er.replace_group(2)).str())
    # col = sf.regexp_replace(col, (er.namedGroup('a', er.number) + er.namedGroup('b', er.anyof(*list('nsew')))).str(), '${a} ${b}')
    # col = sf.regexp_replace(col, (er.group(er.number) + er.group(er.anyof(*list('nsew')))).str(), '\1 \2')
    return col


### Levenstien dist
Apparently there's this thing called Levenstien distance that measures how close 2 strings are. We could alternatively use that instead of the udf (there's a builtin spark function) to join addresses, but that would require a cross join between datasets with sizes of ~6,000 and (number of non-residential places in the US), and then calling sf.levenstien on all of them, which I can't imagine is particularly fast.

You maaaay be able to do something like match them all by county, then cross join & levenstien within that group, but still, yuck.

In [ ]:
# filter places by just LDS meetinghouses
scrapedAddr = addresses\
    .filter(sf.col('_c0') == 'id')\
    .select(formatAddress('_c2').alias('street_address'))

safegraphAddr = places\
    .select(
        'placekey', 'top_category',
        formatAddress('street_address').alias('street_address')
    )

In [ ]:
combAddr = safegraphAddr.join(scrapedAddr, on='street_address', how='inner') \
    .filter(sf.col('top_category') == 'Religious Organizations')
print(f'scraped: {scrapedAddr.count()}, comb: {combAddr.count()}')

scraped: 425 , comb: 178

## Method 2: Join on lat & lon

In [ ]:
precision = 4
scrapedCoord = fullAddr.filter(sf.col('state') == 'id')\
    .select(sf.round(sf.col('lat'), precision).alias('lat'), 
            sf.round(sf.col('lon'), precision).alias('lon'))
safegraphCoord = places.select(
    'placekey', 'top_category',
    sf.round(sf.col('latitude'), precision).alias('lat'), 
    sf.round(sf.col('longitude'), precision).alias('lon'))

In [ ]:
combCoord = safegraphCoord.join(scrapedCoord, on=['lat', 'lon'], how='inner')\
    .filter(sf.col('top_category') == 'Religious Organizations')
print(f'scraped: {scrapedCoord.count()}, comb: {combCoord.count()}')

scraped: 425 , comb: 32

## Method 3: Regex

In [ ]:
combRegex = places.filter(
    (sf.col("top_category") == "Religious Organizations") &
    (sf.col("location_name").rlike("Latter|latter|Saints|saints|LDS|\b[Ww]ard\b")) &
    (sf.col("location_name").rlike("^((?!Reorganized).)*$")) &
    (sf.col("location_name").rlike("^((?!All Saints).)*$")) &
    (sf.col("location_name").rlike("^((?![cC]ath).)*$")) &
    (sf.col("location_name").rlike("^((?![Bb]ody).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]eter).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]atholic).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]res).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]inist).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]ission).)*$")) &
    (sf.col("location_name").rlike("^((?![Ww]orship).)*$")) &
    (sf.col("location_name").rlike("^((?![Rr]ain).)*$")) &
    (sf.col("location_name").rlike("^((?![Bb]aptist).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]eth).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]vang).)*$")) &
    (sf.col("location_name").rlike("^((?![Ll]utheran).)*$")) &
    (sf.col("location_name").rlike("^((?![Oo]rthodox).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]piscopal).)*$")) &
    (sf.col("location_name").rlike("^((?![Tt]abernacle).)*$")) &
    (sf.col("location_name").rlike("^((?![Hh]arvest).)*$")) &
    (sf.col("location_name").rlike("^((?![Aa]ssem).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]edia).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]artha).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]hristian).)*$")) &
    (sf.col("location_name").rlike("^((?![Uu]nited).)*$")) &
    (sf.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (sf.col("location_name").rlike("^((?![Ww]esl).)*$")) &
    (sf.col("location_name").rlike("^((?![C]cosmas).)*$")) &
    (sf.col("location_name").rlike("^((?![Gg]reater).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]rison).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]ommuni).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]lement).)*$")) &
    (sf.col("location_name").rlike("^((?![Vv]iridian).)*$")) &
    (sf.col("location_name").rlike("^((?![Dd]iocese).)*$")) &
    (sf.col("location_name").rlike("^((?![Hh]istory).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]chool).)*$")) &
    (sf.col("location_name").rlike("^((?![Tt]hougt).)*$")) &
    (sf.col("location_name").rlike("^((?![Hh]oliness).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]artyr).)*$")) &
    (sf.col("location_name").rlike("^((?![Jj]ames).)*$")) &
    (sf.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (sf.col("location_name").rlike("^((?![Hh]ouse).)*$")) &
    (sf.col("location_name").rlike("^((?![Gg]lory).)*$")) &
    (sf.col("location_name").rlike("^((?![Aa]nglican).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]oetic).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]anctuary).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]quipping).)*$")) &
    (sf.col("location_name").rlike("^((?![Jj]ohn).)*$")) &
    (sf.col("location_name").rlike("^((?![Aa]ndrew).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]manuel).)*$")) &
    (sf.col("location_name").rlike("^((?![Rr]edeemed).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]erfecting).)*$")) &
    (sf.col("location_name").rlike("^((?![Aa]ngel).)*$")) &
    (sf.col("location_name").rlike("^((?![Aa]rchangel).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]icheal).)*$")) &
    (sf.col("location_name").rlike("^((?![Tt]hought).)*$")) &
    (sf.col("location_name").rlike("^((?![Pp]ariosse).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]osmas).)*$")) &
    (sf.col("location_name").rlike("^((?![Dd]eliverance).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]ociete).)*$")) &
    (sf.col("location_name").rlike("^((?![Tt]emple).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]eminary).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]mployment).)*$")) &
    (sf.col("location_name").rlike("^((?![Ii]nstitute).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc]amp).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]tudent).)*$")) &
    (sf.col("location_name").rlike("^((?![Ee]ducation).)*$")) &
    (sf.col("location_name").rlike("^((?![Ss]ocial).)*$")) &
    (sf.col("location_name").rlike("^((?![Ww]welfare).)*$")) &
    (sf.col("location_name").rlike("^((?![Cc][Ee][Ss]).)*$")) &
    (sf.col("location_name").rlike("^((?![Ff]amily).)*$")) &
    (sf.col("location_name").rlike("^((?![Mm]ary).)*$")) &
    (sf.col("location_name").rlike("^((?![Rr]ussian).)*$")) &
    (sf.col("location_name").rlike("^((?![Bb]eautif).)*$")) &
    (sf.col("location_name").rlike("^((?![Hh]eaven).)*$")) &    
    (sf.col("location_name").rlike("^((?!Inc).)*$")) &
    (sf.col("location_name").rlike("^((?!God).)*$"))
)
print(f'regex found {combRegex.count()}')

regex found 423

## Combine all 3 methods

In [ ]:
# 'zzw-222@5wg-5bt-jjv' -- "Church"
comb = combRegex\
    .join(combCoord.select('placekey'), on='placekey', how='outer')\
    .join(combAddr.select('placekey'), on='placekey', how='outer')
print(f'Total found: {comb.count()}')

nonObvious = (comb
    .filter(sf.col('location_name').isNull())
    .select('placekey')
    .join(places.select('placekey', 'location_name'), on='placekey', how='inner')
    .filter(~sf.col('location_name').rlike('[lL]atter|[sS]aint'))
)
print(f'There are {nonObvious.count()} non-obvious places found')
display(nonObvious)

Total found: 455

There are 10 non-obvious places found

placekey location_name 222-223@3x5-4n2-qmk Coeur d'Alene 3rd Branch Young Single Adults 222-223@5wf-zyt-rhq Church of Christ Presidents Office zzw-222@3x5-4n2-qfz Coeur D'alene 2nd Ward zzw-222@5wg-3nz-vzz Church zzw-222@5wg-5bt-jjv Church zzw-222@5wr-qzn-sdv Cary Ward Family History Center zzy-224@5qn-rf3-td9 Paris Tabernacle zzy-224@5qn-rf3-td9 Paris Tabernacle zzy-224@5qn-rf3-td9 Paris Tabernacle zzy-224@5qn-rf3-td9 Paris Tabernacle

In [ ]:
comb.repartition(1).write.parquet('dbfs:/FileStore/churchPlaces.parquet')
display(comb)

placekey poi_cbg parent_placekey location_name brands safegraph_brand_ids store_id top_category sub_category naics_code open_hours category_tags latitude longitude street_address city region postal_code iso_country_code opened_on closed_on tracking_closed_since websites phone_number wkt_area_sq_meters 222-222@3x5-4j2-cqz null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 Map(Thu -> List(), Sat -> List(), Tue -> List(), Sun -> List(List(9:00, 14:00)), Mon -> List(), Wed -> List(), Fri -> List()) null 47.722601 -116.919083 1824 E 16th Ave Post Falls ID 83854 US null null 2019-07 [] +12083803142 1598.0 222-222@3x5-4n2-qmk 160550012001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 Map(Thu -> List(), Sat -> List(), Tue -> List(), Sun -> List(List(8:30, 15:00)), Mon -> List(), Wed -> List(), Fri -> List()) Churches 47.702578 -116.781765 2801 N 4th St Coeur D Alene ID 83815 US null null 2019-07 ["lds.org"] null 2146.0 222-222@3x5-4n8-q9f null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches,Non-profit 47.721095 -116.775691 5430 N 4th St Coeur D Alene ID 83815 US null null 2019-07 ["lds.org"] +12086643521 168.0 222-222@5w8-z7t-bc5 160599702001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 45.171196 -113.89175 400 S Daisy St Salmon ID 83467 US null null 2019-07 ["lds.org"] +12087563090 2842.0 222-222@5w9-hn5-qcq null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.57606 -116.414069 3145 S Linder Rd Meridian ID 83642 US null null 2019-07 ["lds.org"] +12084010000 295.0 222-222@5w9-hn5-qcq 160010103131 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.57606 -116.414069 3145 S Linder Rd Meridian ID 83642 US null null 2019-07 ["lds.org"] +12084010000 295.0 222-222@5w9-hrg-kpv 160270211001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.640712 -116.612525 18486 Middleton Rd Caldwell ID 83687 US null null 2019-07 [] +12084020150 1668.0 222-222@5w9-j4z-2rk 160270224002 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.485129 -116.526088 7770 Makayla Dr Nampa ID 83686 US null null 2019-07 ["lds.org"] +12084619648 1236.0 222-222@5w9-j4z-2rk null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.485129 -116.526088 7770 Makayla Dr Nampa ID 83686 US null null 2019-07 ["lds.org"] +12084619648 1236.0 222-222@5w9-j6p-p9z 160270210011 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.619075 -116.683381 5622 S Montana Ave Caldwell ID 83607 US null null 2019-07 [] +12084539118 371.0 222-222@5w9-j7k-kj9 160270211001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.635246 -116.55771 8230 Ustick Rd Nampa ID 83687 US null null 2019-07 ["lds.org"] +12083759726 1236.0 222-222@5w9-j9m-jvz null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.574251 -116.214918 2710 W Sunrise Rim Rd Boise ID 83705 US null null 2019-07 ["lds.org"] +12083439883 968.0 222-222@5w9-j9m-sdv 160010017004 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.58113

# Create relevant patterns from comb

In [ ]:
rPatterns = comb.select('placekey')\
    .join(patterns, on='placekey', how='inner')\
    .withColumn('date_range_start', sf.to_date('date_range_start').alias('date_range_start'))
    # .filter(sf.col('date_range_start') == dt.datetime(2019, 2, 1))

In [ ]:
# Use popularity_by_day to get the percentage of people who visit on sunday compared to other days for each church building
ex = rPatterns.select('placekey', 'date_range_start', sf.explode(sf.col('popularity_by_day')))
sunday = ex.filter(sf.col('key') == 'Sunday').groupBy('placekey', 'date_range_start').agg({'value':'sum'}).withColumnRenamed('sum(value)', 'sunday')
weekday = ex.filter(sf.col('key') != 'Sunday').groupBy('placekey', 'date_range_start').agg({'value':'sum'}).withColumnRenamed('sum(value)', 'weekday')
sundayRatio = sunday.join(weekday, on='placekey', how='inner').select(
    'placekey',
    (sf.col('sunday') / (sf.col('weekday') + sf.col('sunday'))).alias('sundayAttendanceRatio'),
)
rPatterns = rPatterns.join(sundayRatio, on='placekey', how='inner')

In [ ]:
display(rPatterns)

placekey date_range_start date_range_end raw_visit_counts raw_visitor_counts distance_from_home median_dwell bucketed_dwell_times related_same_day_brand related_same_month_brand popularity_by_hour popularity_by_day device_type visits_by_day visitor_home_cbgs visitor_home_aggregation visitor_daytime_cbgs normalized_visits_by_state_scaling normalized_visits_by_region_naics_visits normalized_visits_by_region_naics_visitors normalized_visits_by_total_visits sundayAttendanceRatio normalized_visitors_by_state_scaling estimatedAttendance tractcode tract sundayAttendanceRatio 222-222@5w9-jb6-rff 2019-12-01 2020-01-01T00:00:00-07:00 109.0 46.0 5786.0 54.0 Map(5-10 -> 12, 21-60 -> 27, 61-120 -> 11, <5 -> 1, >240 -> 23, 11-20 -> 15, 121-240 -> 20) Map(Petco -> 1, Sonic -> 2, Walmart -> 4, Jared The Galleria of Jewelry -> 1, ULTA Beauty -> 1, TacoTime -> 3, Green Burrito -> 1, Chevron -> 1, Apollo Burgers -> 1, Ross Stores -> 1, Boys & Girls Clubs of America -> 1, Pita Pit -> 1, Taco Bell -> 2, WinCo Foods -> 3, Starbucks -> 2, Kaia FIT -> 2, Fred Meyer Jewelers -> 3, Burger King -> 2, Jacksons Food Stores -> 3, Shell Oil -> 5) Map(Sonic -> 11, Walmart -> 59, Target -> 15, Chevron -> 30, Albertsons -> 13, WinCo Foods -> 39, The Home Depot -> 13, Starbucks -> 20, Fred Meyer Jewelers -> 22, Dutch Bros Coffee -> 15, Sinclair Oil -> 22, Costco -> 17, Walgreens -> 20, Panda Express -> 17, Burger King -> 17, Jacksons Food Stores -> 17, McDonald's -> 28, Stinker Stores -> 15, Shell Oil -> 24, Subway -> 17) List(20, 23, 23, 23, 21, 20, 21, 25, 18, 25, 28, 16, 28, 23, 19, 21, 6, 8, 15, 24, 24, 23, 21, 20) Map(Wednesday -> 16, Monday -> 19, Saturday -> 9, Thursday -> 25, Tuesday -> 13, Friday -> 14, Sunday -> 13) Map(android -> 34, ios -> 10) List(3, 3, 2, 4, 12, 6, 5, 3, 8, 4, 6, 7, 4, 0, 5, 4, 2, 3, 5, 2, 4, 1, 3, 2, 3, 1, 2, 0, 1, 1, 3) Map(160270201001 -> 5, 160010102013 -> 4, 160010023023 -> 5, 160010024102 -> 4, 160010018003 -> 4, 160010014001 -> 4, 160010023021 -> 4, 490351034001 -> 4, 160010024112 -> 4, 160010102253 -> 4) Map(16001002410 -> 4, 16001010332 -> 4, 41045970400 -> 4, 16001002310 -> 4, 16053970300 -> 4, 49035103400 -> 4, 16027021002 -> 4, 16001002312 -> 4, 16027021500 -> 4, 16001010225 -> 4, 16001002302 -> 9, 16001001400 -> 4) Map(160010103353 -> 4, 160010023024 -> 4, 160270215003 -> 4, 160010103321 -> 4, 160010023023 -> 4, 160270219032 -> 4, 160010024102 -> 4) 1756.0120016578337 8.040542035806231E-4 0.0020958717095775 1.3109339225560373E-5 0.0881316098707403 741.0692851033057 65.31162912191296 16001002410 002410 0.11926605504587157 222-222@5w9-jb6-rff 2019-12-01 2020-01-01T00:00:00-07:00 109.0 46.0 5786.0 54.0 Map(5-10 -> 12, 21-60 -> 27, 61-120 -> 11, <5 -> 1, >240 -> 23, 11-20 -> 15, 121-240 -> 20) Map(Petco -> 1, Sonic -> 2, Walmart -> 4, Jared The Galleria of Jewelry -> 1, ULTA Beauty -> 1, TacoTime -> 3, Green Burrito -> 1, Chevron -> 1, Apollo Burgers -> 1, Ross Stores -> 1, Boys & Girls Clubs of America -> 1, Pita Pit -> 1, Taco Bell -> 2, WinCo Foods -> 3, Starbucks -> 2, Kaia FIT -> 2, Fred Meyer Jewelers -> 3, Burger King -> 2, Jacksons Food Stores -> 3, Shell Oil -> 5) Map(Sonic -> 11, Walmart -> 59, Target -> 15, Chevron -> 30, Albertsons -> 13, WinCo Foods -> 39, The Home Depot -> 13, Starbucks -> 20, Fred Meyer Jewelers -> 22, Dutch Bros Coffee -> 15, Sinclair Oil -> 22, Costco -> 17, Walgreens -> 20, Panda Express -> 17, Burger King -> 17, Jacksons Food Stores -> 17, McDonald's -> 28, Stinker Stores -> 15, Shell Oil -> 24, Subway -> 17) List(20, 23, 23, 23, 21, 20, 21, 25, 18, 25, 28, 16, 28, 23, 19, 21, 6, 8, 15, 24, 24, 23, 21, 20) Map(Wednesday -> 16, Monday -> 19, Saturday -> 9, Thursday -> 25, Tuesday -> 13, Friday -> 14, Sunday -> 13) Map(android -> 34, ios -> 10) List(3, 3, 2, 4, 12, 6, 5, 3, 8, 4, 6, 7, 4, 0, 5, 4, 2, 3, 5, 2, 4, 1, 3, 2, 3, 1, 2, 0, 1, 1, 3) Map(160270201001 -> 5, 160010102013 -> 4, 160010023023 -> 5, 160010024102 -> 4, 160010018003 -> 4, 160010014001 -> 4, 160010023021 -> 4, 490351034001

# Calculate Visitors from rPatterns

## Option 1: Calculate normalized visitors

In [ ]:
def getNormalizedVisitors():
    total_visits = sf.col('normalized_visits_by_state_scaling')
    visitsWithPhones = sf.col('raw_visit_counts')
    visitsNoPhones = total_visits - visitsWithPhones
    noPhonesRatio = visitsNoPhones / total_visits

    visitorsWithPhones = sf.col('raw_visitor_counts')
    # Derived from visitorsNoPhones / (visitorsWithPhones + visitorsNoPhones) == noPhonesRatio, and solving for visitorsNoPhones
    visitorsNoPhones = (-visitorsWithPhones * noPhonesRatio) / (noPhonesRatio - 1)
    total_visitors = visitorsNoPhones + visitorsWithPhones

    return total_visitors

if False:
    rPatterns = rPatterns.withColumn('normalized_visitors_by_state_scaling', getNormalizedVisitors())


In [ ]:
if False:
    rPatterns = rPatterns.withColumn('estimatedAttendance', sf.col('normalized_visitors_by_state_scaling') * sf.col('sundayAttendanceRatio'))

### Get rPlaces from rPatterns

In [ ]:
# Get the tract data
if False:
    rPatterns = rPatterns.join(censustract_pkmap.select('placekey', 'tractcode', 'tract'), on='placekey', how='left')
    rPlaces = rPatterns.join(places, on='placekey', how='left')

In [ ]:
if False:
    rPlacesSub = rPlaces.groupBy('tractcode').agg({
        'estimatedAttendance': 'sum',
        'normalized_visitors_by_state_scaling': 'sum',
        'sundayAttendanceRatio': 'mean',
    }).sort('tractcode')
    display(rPlacesSub)

tractcode avg(sundayAttendanceRatio) sum(estimatedAttendance) sum(normalized_visitors_by_state_scaling) null 0.21742179652318988 39503.51948170106 158141.0920605404 16001000100 0.008138440312303439 1901.1298978983161 277903.094423983 16001000302 0.09523809523809522 316.5119151134746 3323.375108691482 16001000500 0.27279247091956355 2747.7714754055296 8500.763405631002 16001000802 0.09068010075566747 222.70711364200974 2455.9645587743853 16001000803 0.49381188118811886 2737.3160963497767 5543.236606141903 16001000804 0.46334586466165406 3575.8337390229735 7717.41804933153 16001000900 0.3452409910453624 7362.925012964562 37062.02292508422 16001001100 0.05399061032863825 3307.911610645232 61268.275918907275 16001001202 0.47032227109370095 6586.009687923166 13900.861474032983 16001001500 0.41467065868263475 2501.2446981596067 6031.882521193563 16001001600 0.03131991051454129 1165.2564455014524 37204.97365279641 16001001700 0.29501413635662305 4158.807202390374 10532.976701013893 16001001800 0.13361169102296452 349.2799692527851 2614.142269876314 16001001900 0.26439271836952805 15528.116228907442 84480.07080138207 16001002000 0.14571397387495097 4905.837956229815 27468.634006486616 16001002221 0.5328947368421053 6217.776941659896 11667.927100398816 16001002222 0.4327496758439791 12880.736901996584 29599.178304482244 16001002312 0.17391304347826084 515.358684427876 2963.3124354602874 16001002410 0.0881316098707403 482.7646513013354 5477.76957676582 16001002411 0.5892857142857143 4154.354542767275 7049.8137695444675 16001002413 0.3484617155980924 12957.626089653724 33684.96505583177 16001010221 0.5972593542726936 17669.470392334 30610.14548809446 16001010223 0.4510135135135135 4065.849772900408 9014.917848528245 16001010224 0.5493749999999998 5989.086249673236 10901.635949348323 16001010225 0.0 0.0 2796.388953140345 16001010313 0.2676778080397583 15051.991554151064 34571.64599216045 16001010321 0.44525318507291184 9849.48465994092 26700.390342469364 16001010322 0.304266846050695 4618.0229508078855 31756.61907709755 16001010331 0.49939893962452825 17897.918467272673 35194.17703084545 16001010334 0.6504460665044608 5981.518731314757 9196.025680437777 16001010335 0.6421940928270043 4260.584884518302 6634.419301122454 16001010401 0.5904723779023219 9379.077711773336 15884.024490854095 16001010504 0.4304123711340208 4166.234130335545 9679.633787845456 16005000300 0.5109664005432711 14912.253149037657 29149.8205899299 16005000400 0.524482584553256 6195.084831393988 11811.80274397641 16005000600 0.0967741935483875 730.3860591801159 7547.32261152788 16005000700 0.3903924221921516 4231.059212538449 10837.964499361919 16005000900 0.12062615101289134 785.3809952180444 6510.8684031053135 16005001000 0.3723849372384937 3180.125318749115 8539.887091921782 16005001101 0.4110821735973811 26321.143813618266 71180.5595354834 16005001200 0.04204729510851959 2004.7938622792046 8506.826787552702 16005001300 0.22203098106712565 2439.144010764456 10985.602094993405 16005001500 0.10826673895364577 2658.045694684612 12523.166604751936 16005001700 0.638052017025699 9922.51742281418 15418.438627172382 16005001900 0.2014026321606284 4620.793444610726 16264.267868778476 16007950100 0.2565391616592004 4591.537772287928 16141.09196696135 16007950200 0.2983425414364639 11374.774596767002 38126.55929657091 16011950100 0.18580701218204806 30068.525019315162 168103.75003024805 16011950400 0.6266233766233765 2822.113525895868 4503.683761533302 16011950500 0.37477578210423296 22387.310594035673 62401.01990736794 16011950600 0.6385442514474774 8694.415757262219 13615.99566130832 16011950700 0.5902309826096235 7566.466133809206 13178.22060204163 16013960100 0.13953488372093023 58.63495181845707 420.2171546989423 16013960200 0.327433628318584 347.0139600415722 1059.799391478315 16013960500 0.6386378757636281 42135.66520473938 66543.71735728571 16017950300 0.5102564102564102 4892.97042106324 9589.238513641529 16019970300 0.445266176560407 19978.83587711599 40540.29303388292

## Option 2: Calculate by visitor_home_aggregation

In [ ]:
final = (
  rPatterns
    .select('sundayAttendanceRatio', 'date_range_start', sf.explode('visitor_home_aggregation'))
    .select('date_range_start', sf.col('key').alias('tractcode'), (sf.col('sundayAttendanceRatio') * sf.col('value')).alias('estimatedMembers'))
    .groupBy('tractcode', 'date_range_start').agg(sf.sum('estimatedMembers').alias('estimatedMembers'))
    .withColumn('tract', sf.substring(sf.rpad(sf.col('tractcode').cast('string'), 11, '0'), 6, 6))
    .groupBy('tract').agg(
      sf.median(sf.col('estimatedMembers')),
      sf.mean(sf.col('estimatedMembers')), 
      sf.min(sf.col('estimatedMembers')), 
      sf.max(sf.col('estimatedMembers')), 
      sf.stddev(sf.col('estimatedMembers')),
      sf.count(sf.col('estimatedMembers')),
    )
    .withColumn('team_name', sf.lit('Marquet'))
    # .withColumnRenamed('median(estimatedMembers)', 'estimatedMembers')
    # .join(tract_table.select('tractcode', 'tract'), on='tractcode', how='left')
    .sort('tract')
)
display(final)

tract median(estimatedMembers) avg(estimatedMembers) min(estimatedMembers) max(estimatedMembers) stddev_samp(estimatedMembers) count(estimatedMembers) team_name 000100 260.47113992669836 411.90871468226845 15.015079426895554 2192.656573291568 474.9399599947735 39 Marquet 000101 801.3687946822783 632.1584579752734 9.425043794309047 1241.642865031498 450.88711854007596 9 Marquet 000102 268.8739262329275 344.27924005754346 127.5575495557855 1011.2019750400239 257.0703635247495 10 Marquet 000105 185.98335288048378 185.98335288048378 185.98335288048378 185.98335288048378 null 1 Marquet 000113 119.94700242374607 119.94700242374607 119.94700242374607 119.94700242374607 0.0 2 Marquet 000132 89.74461123487566 89.74461123487566 89.74461123487566 89.74461123487566 null 1 Marquet 000200 488.1366757733973 1911.428240969746 1.6039915333236667 5947.719073884627 2100.850664501673 58 Marquet 000201 232.50177013322246 230.5668063197096 25.52681237292137 593.4086654253143 150.92172226916497 17 Marquet 000202 325.5075951815573 496.05480408689044 100.68337845950784 1608.2950773956077 442.45485105264936 26 Marquet 000203 252.9777807422294 275.19792588667343 189.4257908225365 460.25848617821583 87.0632678531453 7 Marquet 000204 127.5575495557855 158.70811527529793 127.5575495557855 283.31037815334764 69.65478248640444 5 Marquet 000205 267.0365887726027 277.20586471796213 254.63677300636928 305.2858081648261 20.76376749936633 5 Marquet 000206 367.8711566233928 367.8711566233928 243.3244191625934 492.4178940841922 176.13568526638372 2 Marquet 000207 8.458720802153374 8.458720802153374 8.458720802153374 8.458720802153374 null 1 Marquet 000208 127.5575495557855 127.5575495557855 127.5575495557855 127.5575495557855 null 1 Marquet 000211 313.43925385457266 313.43925385457266 313.43925385457266 313.43925385457266 null 1 Marquet 000215 145.1371980107722 145.1371980107722 145.1371980107722 145.1371980107722 null 1 Marquet 000300 345.8356788049541 1603.5834438772035 7.5448533024046895 6810.436555698474 2319.0680617240464 49 Marquet 000301 89.74461123487566 119.77099380546105 89.74461123487566 308.07813735029424 76.2478783597853 8 Marquet 000302 510.8584523089753 608.6963035379063 14.586749927383634 1532.831832343677 418.6335795728558 22 Marquet 000303 302.1551067019751 326.28522701771465 88.06920296994412 581.7191472751166 186.9340928103975 5 Marquet 000304 624.6503459916438 685.5052896138518 106.35255099339713 1710.214944738453 457.8457731395737 11 Marquet 000400 346.4280241893706 1778.8450051287848 2.0049894166545834 9802.764136040887 2962.4884768187094 54 Marquet 000401 534.2034661442409 525.2000834826725 70.6640408174611 1337.7954906563627 395.87482663908156 19 Marquet 000402 534.2034661442409 645.5115035224547 68.56776279734412 1995.1570174605104 534.9860716970155 17 Marquet 000403 373.28348723375956 407.0622033992475 181.49028381238534 968.5496480678944 231.85910874645944 10 Marquet 000500 734.8744623525668 1309.64255274269 41.22497515049502 4878.190642774655 1397.6187017497616 50 Marquet 000501 237.9345629086028 325.9475967400261 111.4857945660978 968.5496480678944 259.43495317042147 9 Marquet 000502 313.54533292133175 530.9137577846759 100.68337845950784 1251.8600262212422 457.10322619716504 8 Marquet 000503 127.5575495557855 146.70048396815773 127.5575495557855 184.98635279290215 33.156535008187355 3 Marquet 000504 285.2760363411695 361.5001939723263 232.01231623643363 643.4363869705327 189.65702844804616 4 Marquet 000505 267.0365887726027 361.2891957264651 227.68734183653356 745.5878901604096 217.4816012253982 5 Marquet 000506 305.2858081648261 305.2858081648261 305.2858081648261 305.2858081648261 null 1 Marquet 000508 272.5352980692909 272.5352980692909 263.91727147801527 281.15332466056657 12.187730086274 2 Marquet 000509 320.0138379378168 284.35788827680756 203.01914606241974 330.0406808301861 70.6195980826926 3 Marquet 000526 285.595447579006 285.595447579006 285.595447579006 285.595447579006 null 1 Marquet 000600 430.4991059624017 670.525382078

In [ ]:
final.describe().show()

+-------+-----------------+------------------------+---------------------+---------------------+---------------------+-----------------------------+-----------------------+---------+
|summary|            tract|median(estimatedMembers)|avg(estimatedMembers)|min(estimatedMembers)|max(estimatedMembers)|stddev_samp(estimatedMembers)|count(estimatedMembers)|team_name|
+-------+-----------------+------------------------+---------------------+---------------------+---------------------+-----------------------------+-----------------------+---------+
|  count|             1169|                    1169|                 1169|                 1169|                 1169|                          539|                   1169|     1169|
|   mean|488380.6723695466|       523.9070980588267|    574.3034971275939|   275.97017884196345|   1001.7624516022976|            512.8161507614506|      4.704875962360992|     null|
| stddev|281371.7235455154|      1859.2411393607472|   1977.8597617504026|   1353.602

In [ ]:
display(tract_table.select('tractcode', 'tract'))

tractcode tract 16041970200 970200 16041970100 970100 16073950200 950200 16073950101 950101 16073950102 950102 16069960700 960700 16069960900 960900 16069960400 960400 16069960200 960200 16069960300 960300 16069960600 960600 16069940000 940000 16069960500 960500 16069961000 961000 16069960800 960800 16001000500 000500 16001000600 000600 16001002222 002222 16001001500 001500 16001010100 010100 16081960100 960100 16067970500 970500 16067970400 970400 16067970100 970100 16067970200 970200 16067970300 970300 16001010201 010201 16001010322 010322 16001010401 010401 16001001100 001100 16001010223 010223 16001010402 010402 16001002100 002100 16001010331 010331 16071960100 960100 16001001201 001201 16001001000 001000 16001001202 001202 16001000100 000100 16001000302 000302 16001000803 000803 16001000900 000900 16001000802 000802 16001001400 001400 16001002411 002411 16001000400 000400 16001010501 010501 16055001500 001500 16055000200 000200 16055002000 002000 16055001900 001900 16055000100 000100 16055000800 000800 16055001400 001400 16055000700 000700 16055000900 000900 16055001100 001100 16055001200 001200 16055001300 001300 16055000500 000500 16051960100 960100 16051960400 960400 16051960300 960300 16051960200 960200 16083000200 000200 16055001002 001002 16055000402 000402 16001002000 002000 16055000601 000601 16055001001 001001 16001002221 002221 16001002302 002302 16001002310 002310 16001002410 002410 16001002413 002413 16001010221 010221 16001010321 010321 16001010332 010332 16001010333 010333 16001002412 002412 16001010313 010313 16015950200 950200 16037960200 960200 16061950300 950300 16061940001 940001 16061940002 940002 16057005600 005600 16057005100 005100 16057005500 005500 16057005400 005400 16057005200 005200 16057005300 005300 16057005700 005700 16021970100 970100 16021970200 970200 16017950700 950700 16017950800 950800 16017950200 950200 16017950600 950600 16017950400 950400 16017950500 950500 16017950900 950900 16017950100 950100 16017950300 950300 16047960200 960200 16047960100 960100 16085970200 970200 16085970300 970300 16085970100 970100 16005000800 000800 16001001900 001900 16013960200 960200 16013960300 960300 16049940000 940000 16049960100 960100 16049960200 960200 16049960400 960400 16049960300 960300 16013960100 960100 16013960500 960500 16043970100 970100 16043970300 970300 16043970200 970200 16005001101 001101 16005001102 001102 16005001200 001200 16005001400 001400 16005001500 001500 16005001601 001601 16005001602 001602 16005001603 001603 16005000400 000400 16005000700 000700 16027021300 021300 16027021600 021600 16027021700 021700 16027020200 020200 16027020100 020100 16027021200 021200 16027022300 022300 16027022100 022100 16027022200 022200 16027021800 021800 16027021901 021901 16027020402 020402 16027022400 022400 16027020300 020300 16027021500 021500 16027021100 021100 16059970300 970300 16045960100 960100 16045960300 960300 16045960200 960200 16083001500 001500 16077960100 960100 16077960200 960200 16059970100 970100 16019970401 970401 16019971100 971100 16019970402 970402 16019970300 970300 16059970200 970200 16019971400 971400 16019970602 970602 16019970603 970603 16019971500 971500 16019970503 970503 16019970501 970501 16019970100 970100 16019970601 970601 16055001600 001600 16055001800 001800 16055940000 940000 16055001700 001700 16019970403 970403 16019970502 970502 16019970700 970700 16019970800 970800 16019970900 970900 16019971000 971000 16019971200 971200 16019971302 971302 16019971301 971301 16079960200 960200 16079960400 960400 16079960300 960300 16075960300 960300 16075960400 960400 16075960100 960100 16075960200 960200 16029960200 960200 16029960100 960100 16087970100 970100 16087970300 970300 16087970200 970200 16063950100 950100 16001001600 001600 16001001800 001800 16001001700 001700 16027020602 020602 16027020902 020902 16027021002 021002 16027020401 020401 16027020700 020700 16027020901 020901 16027020504 020504 16027021904 021904 16027021903 021903 16027021001 021001 16027020601 0

## Alternate Methods

In [ ]:
dist = rPatterns.join(sundayRatio, on='placekey', how='left')\
    .select(
        'placekey',
        (sf.col('distance_from_home') * sf.col('sunday_ratio')).alias('normalized_dist'),
    )
# small, not mean, because of https://web.archive.org/web/20220526041151/https://docs.safegraph.com/docs/monthly-patterns#section-distance-from-home
# small, not min, because apparently the min is 0
small = dist.agg(sf.percentile_approx(dist.normalized_dist, .25)).collect()[0][0]
dist = dist.fillna(small)\
    .groupBy('placekey').agg({'normalized_dist': 'sum'})\
    .withColumnRenamed('sum(normalized_dist)', 'normalized_dist')
# dist.show()


---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3930947574261965>:1
----> 1 dist = rPatterns.join(sundayRatio, on='placekey', how='left')\
      2     .select(
      3         'placekey',
      4         (sf.col('distance_from_home') * sf.col('sunday_ratio')).alias('normalized_dist'),
      5     )
      6 # small, not mean, because of https://web.archive.org/web/20220526041151/https://docs.safegraph.com/docs/monthly-patterns#section-distance-from-home
      7 # small, not min, because apparently the min is 0
      8 small = dist.agg(sf.percentile_approx(dist.normalized_dist, .25)).collect()[0][0]

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_n